In [1]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm
from matplotlib.ticker import LinearLocator, FormatStrFormatter
import scipy
from brian2.units import *
%matplotlib inline
plt.viridis()

In [2]:
from matplotlib import animation, rc
from IPython.display import HTML

In [3]:
no_iterations = 3000000

# Wiring
n = 16
N = n ** 2
S = np.asarray((n, n))

s_max = 32
sigma_form_forward = 2.5
sigma_form_lateral = 1
p_form_lateral = 1
p_form_forward = 0.16
p_elim_dep = 0.0245
p_elim_pot = 1.36 * np.e ** -4
f_rew = 10 ** 4 * Hz#Hz

# Membrane
v_rest = -70 * mvolt #mV
e_ext = 0 * mvolt #V
v_thr = -54 * mvolt #mV
g_max = 0.2
tau_m = 20* ms #ms
tau_ex = 5* ms #ms
e = np.e
g = g_max
pre_t = 0 * ms


# Inputs
f_mean = 20 * Hz
f_base = 5 * Hz
f_peak = 152.8  * Hz
sigma_stim = 2
t_stim = 0.02 * second
rate = 200 * Hz

# STDP
Apre = a_plus = 0.1
b = 1.2
taupre = tau_plus = 20 * ms #ms
taupost = tau_minus = 64 * ms #ms
Apost = a_minus = (a_plus * tau_plus * b) / tau_minus


In [12]:
def poisson_generator(rate, t_start, t_stop):
    n = int((t_stop - t_start) / 1000.0 * rate)
    number = np.ceil(n + 3 * np.sqrt(n))
    if number < 100:
        number = min(5 + np.ceil(2 * n), 100)

    if number > 0:
        isi = np.random.exponential(1.0 / rate, int(number)) * 1000.0
        if number > 1:
            spikes = np.add.accumulate(isi)
        else:
            spikes = isi
    else:
        spikes = np.array([])

    spikes += t_start
    i = np.searchsorted(spikes, t_stop)

    extra_spikes = []
    if len(spikes) == i:
        # ISI buf overrun

        t_last = spikes[-1] + np.random.exponential(1.0 / rate, 1)[0] * 1000.0

        while (t_last < t_stop):
            extra_spikes.append(t_last)
            t_last += np.random.exponential(1.0 / rate, 1)[0] * 1000.0

            spikes = np.concatenate((spikes, extra_spikes))
    else:
        spikes = np.resize(spikes, (i,))

    # Return spike times, rounded to millisecond boundaries
    return [round(x) for x in spikes]

In [13]:
def distance(x0, x1, grid, type='euclidian'):
    x0 = np.asarray(x0)
    x1 = np.asarray(x1)
    delta = np.abs(x0 - x1)
    delta = np.where(delta > grid * .5, delta - grid, delta)
    
    if type=='manhattan':
        return np.abs(delta).sum(axis=-1)
    return np.sqrt((delta ** 2).sum(axis=-1))

In [14]:
def generate_rates(s, grid):
        '''
        Function that generates an array the same shape as the input layer so that
        each cell has a value corresponding to the firing rate for the neuron
        at that position.
        '''
        _rates = np.zeros(grid)
        for x in range(grid[0]):
            for y in range(grid[1]):
                _d = distance(s, (x, y), grid)
                _rates[x, y] = f_base + f_peak * np.e ** (-_d / (2 * sigma_stim ** 2))
        return _rates * Hz

In [37]:
def generate_spikes(rates):
    spikes = np.zeros((16,16,21))
    for x in range(16):
        for y in range(16):
            spikes_times_xy = poisson_generator(rates[x,y], 0 , 20)
            for time in spikes_times_xy:
                spikes[x,y,int(time)] = 1
    return spikes

In [40]:
grid = np.asarray((16, 16))
s = (5, 15)

In [41]:
input_rates = generate_rates(s, grid)

In [42]:
input_rates.shape

(16, 16)

In [35]:
poisson_generator(100, 0 , 20)

[1.0, 4.0, 11.0, 17.0]

In [20]:
plt.matshow(input_rates/Hz, fignum=160)
plt.grid(visible=False)
plt.colorbar()

In [186]:
# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots(figsize=(15,15))
# ax.set_xlim(( 0, 16))
# ax.set_ylim(( 0, 16))
image = np.zeros((16,16))
line = ax.matshow(input_rates/Hz)
spikes_in_window = generate_spikes(input_rates/Hz)

In [187]:

# initialization function: plot the background of each frame
def init():
#     line.set_data(input_rates/Hz)
    line.set_data(np.zeros((16,16)))
    return (line,)

In [188]:
# animation function. This is called sequentially
def animate(i):
    global image, grid, spikes_in_window
    if i % 20 == 0:
        rates = generate_rates(np.random.randint(0, 16, size=2), grid)
        spikes_in_window = generate_spikes(rates/Hz)
    
    image += spikes_in_window[0:16, 0:16, i%20] * 100
            
    line.set_data(image)
    image *= .85
    return (line,)

In [189]:
# call the animator. blit=True means only re-draw the parts that have changed.
anim = animation.FuncAnimation(fig, animate, init_func=init,
                               frames=500, interval=50, blit=True)

In [190]:
HTML(anim.to_html5_video())

In [192]:
Writer = animation.writers['ffmpeg']
writer = Writer(fps=60, metadata=dict(artist='PAB'), bitrate=1800)

In [193]:
anim.save('im.mp4', writer=writer)